## <b>IBM Data Science Coursera Capstone Final Project Notebook</b>

<b>Topic : Starting a new Italian Restaurant in Toronto</b>

> In this notebook, I will be creating clusters to find the most suitable location to start up an Italian Restaurant in Toron, Canada.

## Step 1: Import Libraries

In [5]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print("Libraries imported.")

Libraries imported.


In [6]:
# send the GET request
data = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M').text

In [7]:
# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(data, 'html.parser')

In [8]:
# create three lists to store table data
postalCodeList = []
boroughList = []
neighborhoodList = []

In [9]:
# append the data into the respective lists
for row in soup.find('table').find_all('tr'):
    cells = row.find_all('td')
    if(len(cells) > 0):
        postalCodeList.append(cells[0].text)
        boroughList.append(cells[1].text)
        neighborhoodList.append(cells[2].text.rstrip('\n')) # avoid new lines in neighborhood cell

In [10]:
# create a new DataFrame from the three lists
toronto_df = pd.DataFrame({"PostalCode": postalCodeList,
                           "Borough": boroughList,
                           "Neighborhood": neighborhoodList})

toronto_df['PostalCode'] = toronto_df['PostalCode'].map(lambda x: x.rstrip('\n'))
toronto_df['Borough'] = toronto_df['Borough'].map(lambda x: x.rstrip('\n'))

toronto_df.head()

PostalCode           Borough               Neighborhood
0        M1A      Not assigned                           
1        M2A      Not assigned                           
2        M3A        North York                  Parkwoods
3        M4A        North York           Victoria Village
4        M5A  Downtown Toronto  Regent Park, Harbourfront

In [11]:
#Check Neighborhood is empty but Borough exists
empty_neighborhood = toronto_df[toronto_df['Neighborhood'].isna()].shape[0]
print(f'Number of rows on which neighborhood column is empty: {empty_neighborhood}')

Number of rows on which neighborhood column is empty: 0


In [12]:
# drop cells with a borough that is Not assigned
toronto_df = toronto_df[toronto_df.Borough != "Not assigned"].reset_index(drop=True)
toronto_df.head()

PostalCode           Borough                                 Neighborhood
0        M3A        North York                                    Parkwoods
1        M4A        North York                             Victoria Village
2        M5A  Downtown Toronto                    Regent Park, Harbourfront
3        M6A        North York             Lawrence Manor, Lawrence Heights
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

## Step 2: Grouping neighbours of the same Borough

In [13]:
#Group neighborhoods by Postcode and Borough
toronto_grouped = toronto_df.groupby(['PostalCode','Borough']).Neighborhood.agg([('Neighborhood', ', '.join)])
toronto_grouped.reset_index(inplace=True)
toronto_grouped.head(5)

PostalCode      Borough                            Neighborhood
0        M1B  Scarborough                          Malvern, Rouge
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2        M1E  Scarborough       Guildwood, Morningside, West Hill
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

In [14]:
#Drop the the rows on which the Borough is empty
toronto_grouped.dropna(subset=['Borough'], inplace=True)

In [15]:
#Lets check if Neighborhood is empty but Borough exists
empty_neighborhood = toronto_grouped[toronto_grouped['Neighborhood'].isna()].shape[0]
print(f'Number of rows on which Neighborhood column is empty: {empty_neighborhood}')

Number of rows on which Neighborhood column is empty: 0


In [16]:
print('The shape of the dataset is:',toronto_grouped.shape)

The shape of the dataset is: (103, 3)


In [17]:
#to make it easier, we will store this in csv format.
#Export to .CSV
toronto_grouped.to_csv('Toronto_PostcodesData.csv')

In [18]:
#Read CSV file from link and load into dataframe
url_csv = 'http://cocl.us/Geospatial_data'
toronto_coordinates = pd.read_csv(url_csv)
toronto_coordinates.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [19]:
#use the previously cleaned data
toronto_neighborhood = pd.read_csv('Toronto_PostcodesData.csv',index_col=[0])
toronto_neighborhood.head()

PostalCode      Borough                            Neighborhood
0        M1B  Scarborough                          Malvern, Rouge
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2        M1E  Scarborough       Guildwood, Morningside, West Hill
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

In [25]:
# Make sure both dataframes have the same 
toronto_coordinates.rename(columns={'Postal Code': 'PostalCode'}, inplace=True)
toronto_neighborhood.rename(columns={'Postcode': 'PostalCode'}, inplace=True)

In [26]:
# Merge both datasets
toronto_neighborhood_coordinates = pd.merge(toronto_neighborhood, toronto_coordinates, on='PostalCode')
toronto_neighborhood_coordinates.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [28]:
#Export to .CSV
toronto_neighborhood_coordinates.to_csv('Toronto_Postcodes_2.csv')

## Step 2: Create Clusters of our neighborhood and visualize it with Folium

In [29]:
# Read .csv file from above
new_df = pd.read_csv('Toronto_Postcodes_2.csv', index_col=0)
new_df.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [31]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(new_df['Borough'].unique()),
        new_df.shape[0]
    )
)

The dataframe has 10 boroughs and 103 neighborhoods.


In [32]:
new_df.rename(columns={'Neighbourhood': 'Neighborhood'}, inplace=True)

In [33]:
#count Bourough and Neighborhood
new_df.groupby('Borough').count()['Neighborhood']

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
East York            5
Etobicoke           12
Mississauga          1
North York          24
Scarborough         17
West Toronto         6
York                 5
Name: Neighborhood, dtype: int64

In [35]:
new_df_toronto = new_df[new_df['Borough'].str.contains('Toronto')]
new_df_toronto.reset_index(inplace=True)
new_df_toronto.drop('index', axis=1, inplace=True)
new_df_toronto.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/pandas/core/frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


PostalCode          Borough                    Neighborhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  India Bazaar, The Beaches West  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [36]:
#Check the number of neighborhoods
print(new_df_toronto.groupby('Borough').count()['Neighborhood'])

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
West Toronto         6
Name: Neighborhood, dtype: int64


In [37]:
#Create list with the Boroughs (to be used later)
boroughs = new_df_toronto['Borough'].unique().tolist()

In [38]:
#Obtain the coordinates from the dataset itself, just averaging Latitude/Longitude of the current dataset 
lat_toronto = new_df_toronto['Latitude'].mean()
lon_toronto = new_df_toronto['Longitude'].mean()
print('The geographical coordinates of Toronto are {}, {}'.format(lat_toronto, lon_toronto))

The geographical coordinates of Toronto are 43.66713498717947, -79.38987324871795


In [39]:
#Selecting a random colour

borough_color = {}
for borough in boroughs:
    borough_color[borough]= '#%02X%02X%02X' % tuple(np.random.choice(range(256), size=3)) #Random color

In [40]:
map_toronto = folium.Map(location=[lat_toronto, lon_toronto], zoom_start=12)

# add markers to map
for lat, lng, borough, neighborhood in zip(new_df_toronto['Latitude'], 
                                           new_df_toronto['Longitude'],
                                           new_df_toronto['Borough'], 
                                           new_df_toronto['Neighborhood']):
    label_text = borough + ' - ' + neighborhood
    label = folium.Popup(label_text)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color=borough_color[borough],
        fill_color=borough_color[borough],
        fill_opacity=0.7).add_to(map_toronto)  
    
map_toronto

## Retrieve Venue data using Foursquare

In [42]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)


In [43]:
#Get venues for all neighborhoods in our dataset
toronto_venues = getNearbyVenues(names=new_df_toronto['Neighborhood'],
                                latitudes=new_df_toronto['Latitude'],
                                longitudes=new_df_toronto['Longitude'])

The Beaches
The Danforth West, Riverdale
India Bazaar, The Beaches West
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park, Summerhill East
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
Rosedale
St. James Town, Cabbagetown
Church and Wellesley
Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North & West
The Annex, North Midtown, Yorkville
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Stn A PO Boxes
First Canadian Place, Underground city
Christie
Dufferin, Dovercourt Village
Little Portugal, Trinity
Brockton, Parkdale Village, Exhibition Place
High Park, The Junction South
Parkdale, Ron

In [44]:
#Check size of resulting dataframe
toronto_venues.shape

(1614, 7)

In [45]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  The Beaches              43.676357              -79.293031   
1  The Beaches              43.676357              -79.293031   
2  The Beaches              43.676357              -79.293031   
3  The Beaches              43.676357              -79.293031   
4  The Beaches              43.676357              -79.293031   

                                Venue  Venue Latitude  Venue Longitude  \
0                   Glen Manor Ravine       43.676821       -79.293942   
1  The Big Carrot Natural Food Market       43.678879       -79.297734   
2                 Grover Pub and Grub       43.679181       -79.297215   
3                   Glen Stewart Park       43.675278       -79.294647   
4                       Upper Beaches       43.680563       -79.292869   

      Venue Category  
0              Trail  
1  Health Food Store  
2                Pub  
3               Park  
4       Neighborhood

In [46]:
#Number of venues per neighborhood
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            57   
Brockton, Parkdale Village, Exhibition Place                           22   
Business reply mail Processing Centre                                  17   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Central Bay Street                                                     64   
Christie                                                               17   
Church and Wellesley                                                   75   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             38   
Davisville North                                                        7   
Dufferin, Dovercourt Village                                           16   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                                4   
Garden District, Ryerson                                              100   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          22   
India Bazaar, The Beaches West                                         22   
Kensington Market, Chinatown, Grange Park                              56   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               41   
Moore Park, Summerhill East                                             3   
North Toronto West                                                     24   
Parkdale, Roncesvalles                                                 14   
Queen's Park, Ontario Provincial Government                            35   
Regent Park, Harbourfront                                              45   
Richmond, Adelaide, King                                               93   
Rosedale                                                                4   
Roselawn                                                                2   
Runnymede, Swansea                                                     40   
St. James Town                                                         78   
St. James Town, Cabbagetown                                            43   
Stn A PO Boxes                                                         94   
Studio District                                                        41   
Summerhill West, Rathnelly, South Hill, Forest ...                     16   
The Annex, North Midtown, Yorkville                                    24   
The Beaches                                                             5   
The Danforth West, Riverdale                                           42   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         34   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             57   
Brockton, Parkdale Village, Exhibition Place                            22   
Business reply mail Processing Centre                                   17   
CN Tower, King and Spadina, Railway Lands, Harb...                      16   
Central Bay Street                                                      64   
Christie                                                                17   
Church and Wellesley                                                    75   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              38   
Davisville North                    

In [47]:
#Number of unique venue categories
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 234 uniques categories.


In [48]:
#print out the list of categories
toronto_venues['Venue Category'].unique()[:100]

array(['Trail', 'Health Food Store', 'Pub', 'Park', 'Neighborhood',
       'Cosmetics Shop', 'Greek Restaurant', 'Italian Restaurant',
       'Ice Cream Shop', 'Yoga Studio', 'Brewery',
       'Fruit & Vegetable Store', 'Dessert Shop', 'Restaurant',
       'Pizza Place', 'Juice Bar', 'Bookstore', 'Bubble Tea Shop',
       'Furniture / Home Store', 'Grocery Store', 'Spa', 'Coffee Shop',
       'Bakery', 'Caribbean Restaurant', 'Café', 'Indian Restaurant',
       'Lounge', 'Frozen Yogurt Shop', 'American Restaurant',
       'Liquor Store', 'Gym', 'Fish & Chips Shop', 'Fast Food Restaurant',
       'Sushi Restaurant', 'Pet Store', 'Steakhouse', 'Burrito Place',
       'Movie Theater', 'Sandwich Place', 'Intersection',
       'Food & Drink Shop', 'Fish Market', 'Gay Bar',
       'Seafood Restaurant', 'Cheese Shop', 'Middle Eastern Restaurant',
       'Comfort Food Restaurant', 'Stationery Store', 'Wine Bar',
       'Thai Restaurant', 'Coworking Space', 'Latin American Restaurant',
       '

In [50]:
# check if the results contain "Italian Restaurants"
"Italian Restaurant" in toronto_venues['Venue Category'].unique()

True

<b>Analyzing each neighborhood</b>

In [51]:
# one hot encoding
to_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(1614, 235)


Neighborhoods  Afghan Restaurant  Airport  Airport Food Court  \
0   The Beaches                  0        0                   0   
1   The Beaches                  0        0                   0   
2   The Beaches                  0        0                   0   
3   The Beaches                  0        0                   0   
4   The Beaches                  0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  \
0                 0                   0              0          0           0   
1                 0                   0              0          0           0   
2                 0                   0              0          0           0   
3                 0                   0              0          0           0   
4                 0                   0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  \
0           0       0     0    0                 0                   0      0   
1           0       0     0    0                 0                   0      0   
2           0       0     0    0                 0                   0      0   
3           0       0     0    0                 0                   0      0   
4           0       0     0    0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0                0         0           0                   0   
1                0         0           0                   0   
2                0         0           0                   0   
3                0         0           0                   0   
4                0         0           0                   0   

   Bike Rental / Bike Share  Bistro  Boat or Ferry  Bookstore  Boutique  \
0                         0       0              0          0         0   
1                         0       0              0          0         0   
2                         0       0              0          0         0   
3                         0       0              0          0         0   
4                         0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0                     0               0        0                0         0   
1                     0               0        0                0         0   
2                     0               0        0                0         0   
3                     0               0        0                0         0   
4                     0               0        0                0         0   

   Burger Joint  Burrito Place  Bus Line  Butcher  Café  \
0             0              0         0        0     0   
1             0              0         0        0     0   
2             0              0         0        0     0   
3             0              0         0        0     0   
4             0              0         0        0     0   

   Cajun / Creole Restaurant  Candy Store  Ca

Next, let's group rows by neighborhood and get mean of frequency of occurrence for each category

In [52]:
to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(39, 235)


Neighborhoods  Afghan Restaurant  \
0                                         Berczy Park           0.000000   
1        Brockton, Parkdale Village, Exhibition Place           0.000000   
2               Business reply mail Processing Centre           0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
4                                  Central Bay Street           0.000000   
5                                            Christie           0.000000   
6                                Church and Wellesley           0.013333   
7                      Commerce Court, Victoria Hotel           0.000000   
8                                          Davisville           0.000000   
9                                    Davisville North           0.000000   
10                       Dufferin, Dovercourt Village           0.000000   
11             First Canadian Place, Underground city           0.000000   
12                           Forest Hill North & West           0.000000   
13                           Garden District, Ryerson           0.000000   
14  Harbourfront East, Union Station, Toronto Islands           0.000000   
15                      High Park, The Junction South           0.000000   
16                     India Bazaar, The Beaches West           0.000000   
17          Kensington Market, Chinatown, Grange Park           0.000000   
18                                      Lawrence Park           0.000000   
19                           Little Portugal, Trinity           0.000000   
20                        Moore Park, Summerhill East           0.000000   
21                                 North Toronto West           0.000000   
22                             Parkdale, Roncesvalles           0.000000   
23        Queen's Park, Ontario Provincial Government           0.000000   
24                          Regent Park, Harbourfront           0.000000   
25                           Richmond, Adelaide, King           0.000000   
26                                           Rosedale           0.000000   
27                                           Roselawn           0.000000   
28                                 Runnymede, Swansea           0.000000   
29                                     St. James Town           0.000000   
30                        St. James Town, Cabbagetown           0.000000   
31                                     Stn A PO Boxes           0.000000   
32                                    Studio District           0.000000   
33  Summerhill West, Rathnelly, South Hill, Forest...           0.000000   
34                The Annex, North Midtown, Yorkville           0.000000   
35                                        The Beaches           0.000000   
36                       The Danforth West, Riverdale           0.000000   
37           Toronto Dominion Centre, Design Exchange           0.000000   
38                     University of Toronto, Harbord           0.000000   

    Airport  Airport Food Court  Airport Lounge  Airport Service  \
0    0.0000              0.0000           0.000            0.000   
1    0.0000              0.0000           0.000            0.000   
2    0.0000              0.0000           0.000            0.000   
3    0.0625              0.0625           0.125            0.125   
4    0.0000              0.0000           0.000            0.000   
5    0.0000              0.0000           0.000            0.000   
6    0.0000              0.0000           0.000            0.000   
7    0.0000              0.0000           0.000            0.000   
8    0.0000              0.0000           0.000            0.000   
9    0.0000              0.0000           0.000            0.000   
10   0.0000              0.0000           0.000            0.000   
11   0.0000              0.0000           0.000            0.000   
12   0.0000              0.0000           0.000            0.000   
13   0.0000              0.0000           0.000

In [53]:
len(to_grouped[to_grouped["Italian Restaurant"] > 0])

22

<b>Create a new data frame to find Asian Restaurants only</b>

In [54]:
to_italian = to_grouped[["Neighborhoods","Italian Restaurant"]]

In [55]:
to_italian.head()

Neighborhoods  Italian Restaurant
0                                        Berczy Park            0.000000
1       Brockton, Parkdale Village, Exhibition Place            0.045455
2              Business reply mail Processing Centre            0.000000
3  CN Tower, King and Spadina, Railway Lands, Har...            0.000000
4                                 Central Bay Street            0.062500

## Step 3: Cluster Neighborhoods

Use k-means to cluster the neighborhoods in Toronto into 3 clusters.

In [56]:
# set number of clusters
toclusters = 3

to_clustering = to_italian.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 1, 0, 0, 1, 1, 0, 2, 1, 0], dtype=int32)

In [57]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
to_merged = to_italian.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [58]:
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head()

Neighborhood  Italian Restaurant  \
0                                        Berczy Park            0.000000   
1       Brockton, Parkdale Village, Exhibition Place            0.045455   
2              Business reply mail Processing Centre            0.000000   
3  CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
4                                 Central Bay Street            0.062500   

   Cluster Labels  
0               0  
1               1  
2               0  
3               0  
4               1

In [59]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
to_merged = to_merged.join(toronto_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(1614, 9)


Neighborhood  Italian Restaurant  Cluster Labels  Neighborhood Latitude  \
0  Berczy Park                 0.0               0              43.644771   
0  Berczy Park                 0.0               0              43.644771   
0  Berczy Park                 0.0               0              43.644771   
0  Berczy Park                 0.0               0              43.644771   
0  Berczy Park                 0.0               0              43.644771   

   Neighborhood Longitude                                      Venue  \
0              -79.373306                                       LCBO   
0              -79.373306       The Keg Steakhouse + Bar - Esplanade   
0              -79.373306                             Fresh On Front   
0              -79.373306                              Meridian Hall   
0              -79.373306  Hockey Hall Of Fame (Hockey Hall of Fame)   

   Venue Latitude  Venue Longitude                 Venue Category  
0       43.642944       -79.372440                   Liquor Store  
0       43.646712       -79.374768                     Restaurant  
0       43.647815       -79.374453  Vegetarian / Vegan Restaurant  
0       43.646292       -79.376022                   Concert Hall  
0       43.646974       -79.377323                         Museum

In [60]:
# sort the results by Cluster Labels
print(to_merged.shape)
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged

(1614, 9)


Neighborhood  Italian Restaurant  \
0                                         Berczy Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
12                           Forest Hill North & West            0.000000   
12                           Forest Hill North & West            0.000000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
12                           Forest Hill North & West            0.000000   
12                           Forest Hill North & West            0.000000   
11             First Canadian Place, Underground city            0.010000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinat

## Step 4: Visualize the Clusters

In [61]:
# create map
map_clusters = folium.Map(location=[lat_toronto, lon_toronto], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [62]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

## Step 5: Examine The Clusters

<b>First Cluster</b>

In [63]:
to_merged.loc[to_merged['Cluster Labels'] == 0]

Neighborhood  Italian Restaurant  \
0                                         Berczy Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
12                           Forest Hill North & West            0.000000   
12                           Forest Hill North & West            0.000000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
11             First Canadian Place, Underground city            0.010000   
12                           Forest Hill North & West            0.000000   
12                           Forest Hill North & West            0.000000   
11             First Canadian Place, Underground city            0.010000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinatown, Grange Park            0.000000   
17          Kensington Market, Chinat

<b>Second Cluster</b>

In [64]:
to_merged.loc[to_merged['Cluster Labels'] == 1]

Neighborhood  Italian Restaurant  \
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
8                                     Davisville            0.052632   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
4                             Central Bay Street            0.062500   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
22                        Parkdale, Roncesvalles            0.071429   
22                        Parkdale, Roncesvalles            0.071429   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
5                                       Christie            0.058824   
22                        Parkdale, Roncesvalles            0.071429   
22                        Parkdale, Roncesvalles            0.071429   
22                        Parkdale, Roncesvalles            0.071429   
4                             Central Bay Street            0.062500   
22                        Parkdale, Roncesvalles            0.071429   
22                        Parkdale, Roncesvalles            0.071429   
22                        Parkdale, Roncesvalles            0.071429   
22                        Parkdale, Roncesvalles            0.071429   
22  

<b>Third Cluster</b>

In [65]:
to_merged.loc[to_merged['Cluster Labels'] == 2]

Neighborhood  Italian Restaurant  \
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
32                                    Studio District            0.024390   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
31                                     Stn A PO Boxes            0.031915   
32                                    Studio District            0.024390   
31                                     Stn A PO Boxes            0.031915   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
32                                    Studio District            0.024390   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
32                                    Studio District            0.024390   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court, Victoria Hotel            0.030000   
7                      Commerce Court

## <b>Observations</b>
- The second and third clusters are heavily populated with Italian Restaurants which are in places like <b>Central Bay Street, Roncesvalles, Riverdale, Christie, Harbord, Runnymede(Swansea), Cabbagetown, Toronto Dominion Center, Commerce Court(Victoria Hotel), Toronto Islands, and Garden District(Ryerson)</b> to name a few.
    
- So standing on the fact that there is a heated competition going on in the above mentioned places, I would advice the Italian Chef to look at places like:
   - Kensington Market, Chinatown, and
   - First Canada Place, UnderGround City to target a higher population and if the food is good and their is good customer service, it would make the restaurant grown rapidly
   
- Other alternatives are:
   - North Toronto West,
   - Davisville North, and
   - Yorkville
   
- Adelaide has a Latin Restaurant, choosing a location around or in this region can sprout a dangerous rivalry that if not sturdy enough might wreck the new restaurant that the Italian Chef wants to start up there in a short time.